# **\[SOLAR\]** SIMULATION (GConvGRU+ // STOP)

JiyunLim  
2024-12-12

> INCREMENTAL // 2023.08.14 중단

## Data

In [1]:
import pandas as pd
import numpy as np
import os

In [2]:
# read dataframe 
df = pd.read_csv('data_eng_230710.csv')

# make y, y_upper, y_period, time, regions 
y = df.loc[:,'Bukchoncheon':'Gyeongju-si'].to_numpy()
yU = df.loc[:,'Bukchoncheon_Upper':'Gyeongju-si_Upper'].to_numpy()
yP = np.divide(y, yU+1e-10)
t = df.loc[:,'date']
regions = list(df.loc[:,'Bukchoncheon':'Gyeongju-si'].columns)

TRAIN_RATIO = 0.8
T,N = len(t),len(regions) 
LEN_TEST = int(np.floor(T*(1-TRAIN_RATIO)))
LEN_TR = T - LEN_TEST

## GConvGRU

In [3]:
%run model/gconvgru

In [4]:
s1 = Simulator()

In [5]:
class GConv_GRU(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GConv_GRU, self).__init__()
        self.recurrent = GConvGRU(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight):
        h = self.recurrent(x, edge_index, edge_weight)
        h = F.relu(h)
        h = self.linear(h)
        return h

In [ ]:
s1.simulate(
    n_iteration = 30,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = GConv_GRU
)

method:classic lag:4 filters:4 epoch:50 is done
method:classic lag:4 filters:8 epoch:50 is done
method:classic lag:4 filters:16 epoch:50 is done
method:classic lag:4 filters:32 epoch:50 is done
method:classic lag:8 filters:4 epoch:50 is done
method:classic lag:8 filters:8 epoch:50 is done
method:classic lag:8 filters:16 epoch:50 is done
method:classic lag:8 filters:32 epoch:50 is done
method:proposed lag:8 filters:16 epoch:50 is done
method:proposed lag:8 filters:32 epoch:50 is done
method:proposed lag:12 filters:4 epoch:50 is done
method:proposed lag:12 filters:8 epoch:50 is done
method:proposed lag:12 filters:16 epoch:50 is done
method:proposed lag:12 filters:32 epoch:50 is done
save results
method:classic lag:4 filters:4 epoch:50 is done
method:classic lag:4 filters:8 epoch:50 is done
method:classic lag:4 filters:16 epoch:50 is done
method:classic lag:4 filters:32 epoch:50 is done
method:classic lag:8 filters:4 epoch:50 is done
method:classic lag:8 filters:8 epoch:50 is done
method:

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)


In [7]:
print('stop')

stop

In [ ]:
%run model/lstm

In [ ]:
s2 = Simulator()
s3 = Simulator()
s4 = Simulator()

In [ ]:
class GConv_LSTM(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GConv_LSTM, self).__init__()
        self.recurrent = GConvLSTM(in_channels = node_features, out_channels = filters, K = 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h, c):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h, c)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [ ]:
class GC_LSTM(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GC_LSTM, self).__init__()
        self.recurrent = GCLSTM(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h, c):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h, c)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [ ]:
class LR_GCN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(LR_GCN, self).__init__()
        self.recurrent = LRGCN(node_features, filters, 1, 1)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h_0, c_0):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h_0, c_0)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [ ]:
s2.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = GConv_LSTM
)


s3.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = GC_LSTM
)

s4.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = LR_GCN
)

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

In [ ]:
%run model/tgcn

In [ ]:
s5 = Simulator()

In [ ]:
class T_GCN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(T_GCN, self).__init__()
        self.recurrent = TGCN(node_features, filters)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, prev_hidden_state):
        h = self.recurrent(x, edge_index, edge_weight, prev_hidden_state)
        y = F.relu(h)
        y = self.linear(y)
        return y, h

In [ ]:
s5.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = T_GCN
)

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## RSLT

In [ ]:
df_ = pd.concat([pd.read_csv(fname) for fname in fnames]).reset_index(drop=True)

In [ ]:
df_

In [ ]:
df_.groupby(by=['model','method']).agg({'mse':[np.mean, np.std]})